In [1]:
%matplotlib widget

from matplotlib import pyplot as plt
import numpy as np
import pandas as pd
import datetime

In [2]:
annotations_path = "BARBIES_seagrassOccurence_annotated_Lassing_Video.csv"
revised_path = "BARBIES_seagrassOccurence_annotated_Lassing_Video_revised.csv"
video_path = "Lassing_06252024-173357.avi"

timestamp_field = "eventTime  (TimeStamp for your video?)"

revise_fields = [
    "scientificName",
    "SppPrecentCover",
    "PercentCover"
]

In [3]:
annotations_df = pd.read_csv(annotations_path, sep=",", skiprows=[1], encoding="latin1")
#annotations_df

In [7]:
def parse_custom_timestamp(ts):
    # Format: HH:MM:SS:FF (FF = frames)
    try:
        h, m, s, f = map(int, ts.split(":"))
        # Convert frames (assuming 3 fps) to fractional seconds
        total_seconds = h * 3600 + m * 60 + s + f / 3
        return total_seconds
    except Exception as e:
        print(f"Could not parse timestamp '{ts}': {e}")
        return None

# Example usage
parsed_time = parse_custom_timestamp("00:21:59:04")
print(parsed_time)


1320.3333333333333


In [5]:
from PIL import Image, ImageEnhance
from moviepy.editor import VideoFileClip
from IPython.display import Video
import os

def increase_saturation(frame, factor=1.2):
    """
    Increase the color saturation of a video frame.

    Parameters:
        frame (np.ndarray): The input video frame as a NumPy array.
        factor (float): The enhancement factor for saturation (default 1.2).

    Returns:
        np.ndarray: The saturation-enhanced frame as a NumPy array.
    """
    img = Image.fromarray(frame)
    enhancer = ImageEnhance.Color(img)
    img_enhanced = enhancer.enhance(factor)
    return np.array(img_enhanced)

def show_clip(video_path, annotations, sample_nr, cliplength=10, width=1024):
    t = parse_custom_timestamp(annotations[timestamp_field][sample_nr])
    if t is None:
        print(f"Invalid timestamp for sample {sample_nr}.")
        return None

    clip = VideoFileClip(video_path)
    clip = clip.fl_image(lambda frame: increase_saturation(frame, factor=1.15))
    subclip = clip.subclip(t - cliplength/2, t + cliplength/2)
    os.makedirs("tmp",exist_ok=True)
    temp_path = f"tmp/temp_clip_{sample_nr}.mp4"
    subclip.write_videofile(temp_path, codec="libx264", audio=False, verbose=False, logger=None)
    print(f"Sample {sample_nr}")
    print(f"Timestamp: {t} seconds ({annotations[timestamp_field][sample_nr]})")
    return Video(temp_path, width=width, embed=True)

In [10]:
import ipywidgets as widgets
from IPython.display import display, clear_output

class SampleReviewer:
    def __init__(self, video_path, annotations, cliplength=10, width=1024):
        self.video_path = video_path
        self.annotations = annotations
        self.timestamp_field = timestamp_field
        self.cliplength = cliplength
        self.width = width
        self.sample_nr = 0
        self.max_sample = len(annotations) - 1
        self.revise_fields = revise_fields

        # Widgets
        self.prev_btn = widgets.Button(description="Previous")
        self.next_btn = widgets.Button(description="Next")
        self.sample_nr_box = widgets.BoundedIntText(
            value=self.sample_nr, min=0, max=self.max_sample, description="Sample #"
        )
        # Create a widget for each field in revise_fields
        self.field_boxes = {}
        for field in self.revise_fields:
            val = self.annotations[field].iloc[self.sample_nr] if field in self.annotations.columns else ""
            val = "" if pd.isna(val) else str(val)
            self.field_boxes[field] = widgets.Text(
                value=val,
                description=field
            )
        self.update_btn = widgets.Button(description="Update")

        # Events
        self.prev_btn.on_click(self.on_prev)
        self.next_btn.on_click(self.on_next)
        self.sample_nr_box.observe(self.on_sample_nr_change, names='value')
        self.update_btn.on_click(self.on_update)

        # Layout: navigation row and revision row
        self.controls_nav = widgets.HBox([
            self.prev_btn, self.next_btn, self.sample_nr_box
        ])
        self.controls_fields = widgets.HBox([
            *self.field_boxes.values(), self.update_btn
        ])
        self.controls = widgets.VBox([
            self.controls_nav, self.controls_fields
        ])
        self.output = widgets.Output()
        display(self.output)
        display(self.controls)
        self.show_sample()

    def show_sample(self):
        self.sample_nr_box.value = self.sample_nr
        for field in self.revise_fields:
            val = self.annotations[field].iloc[self.sample_nr] if field in self.annotations.columns else ""
            self.field_boxes[field].value = "" if pd.isna(val) else str(val)
            
        with self.output:
            clear_output(wait=True)
            html = show_clip(self.video_path, self.annotations, self.sample_nr, cliplength=self.cliplength, width=self.width)
            if html is not None:
                display(html)

    def on_prev(self, b):
        if self.sample_nr > 0:
            self.sample_nr -= 1
            self.show_sample()

    def on_next(self, b):
        if self.sample_nr < self.max_sample:
            self.sample_nr += 1
            self.show_sample()

    def on_sample_nr_change(self, change):
        val = change['new']
        if 0 <= val <= self.max_sample:
            self.sample_nr = val
            self.show_sample()

    def on_update(self, b):
        for field in self.revise_fields:
            new_val = self.field_boxes[field].value
            self.annotations.at[self.sample_nr, field] = new_val
        with self.output:
            print(f"Updated fields for sample {self.sample_nr}:")
            for field in self.revise_fields:
                print(f"  {field}: '{self.field_boxes[field].value}'")

# Usage:
SampleReviewer(video_path, annotations_df, 10, 1024)

Output()

In [9]:
# safe updates
annotations_df.to_csv(revised_path, sep=",", index=False, encoding="latin1")